 *Import necessary packages*

In [0]:
# Import necessary packages
from pyspark.sql.functions import udf, col, concat, lit, lower, explode, split, regexp_replace, instr
from pyspark.ml.feature import Tokenizer, StopWordsRemover, IDF, CountVectorizer, StringIndexer
from nltk.stem import PorterStemmer
from pyspark.sql.functions import lower, regexp_replace, collect_list
from pyspark.sql.types import *

#### Load the 'posts' data from the Databricks local file system into a DataFrame.


In [0]:
# Load data 
posts = spark.read.parquet("/tmp/project/posts")


*displays the contents of the `posts`*

In [0]:
display(posts)

id AcceptedAnswerId AnswerCount Body CommentCount CreationDate FavoriteCount LastEditDate LastEditorDisplayName LastEditorUserId OwnerUserId ParentId PostTypeId Score Tags Title ViewCount 10531977 10532485 1 Ok, capturing key codes from special symbols produces different results on keyboards with different layouts. But how about the 'common' characters, like a-z? If you have a QWERTY-keyboard, you'd get key code 81 when you type q . When you have an AZERTY-keyboard, do you get code 81 when you press a , since a is where q 'should' be? Or is the mapping done differently? EDIT: The answer I accepted is probably the best solution when you're capturing keys and want to be sure 'a' is really 'a', but as I explain in the comment underneath that, I still am curious how the key codes are 'translated' when using int'l keyboards. That is: sources suggest at least a-z should be consistent, but I cannot find support for this (or someone who actually tried). 2 2024-05-10 1 2024-05-14 NULL 1005334 1005334 0 1 2.0 Key code for common characters on international keyboards 2169 10527274 0 0 To get the api to return JSON change the parameter client=t to client=p 3 2024-05-10 0 2024-05-14 NULL 215068 1386085 6599098 2 9.0 NULL NULL 0 10534618 0 0 Those tags are used by the Pervasive Integration tools. After having contacted Pervasive, I have confirmed these tags are not publicly documented. A potential user must contact Pervasive (http://www.pervasiveintegration.com). 0 2024-05-10 0 2024-05-14 NULL 314193 314193 10533159 2 0.0 NULL NULL 0 10510574 0 2 I have an application running Python 2.6.X. Starting the Python interpreter in interactive mode (with or without using virtualenv): readline support working (command history). Starting my application with the same Python interpreter (virtualenv-ed or not): no readline support available when using pdb.set_trace() : cursor keys not working. Operating system is Linux. 0 2024-05-09 0 2024-05-14 NULL 1897 2665694 0 1 12.0 No readline support while using pdb.set_trace() 872 10530232 10576535 2 I know there are a lot of questions targeting this issue. Although there are many good naming convention suggestions out there, we had a debate in our team. A team member insist that we should name our table's like that: sProducts and the primary key like that: ProductGuid There are two prefixe's in his system (s, h) so s stands for static and h - sorry i really don't know. I can see absolutely no logic in there. He says that every big oracle and ibm system is working like that. I've never worked with a oracle or ibm system, so is there a convention for adding prefixes like s and h? And what do they stand for? Somebody out there, who does the same? I'm sorry for that question - but I don't want to always add an s and have no clue why... 3 2024-05-10 1 2024-05-14 NULL 374988 374988 0 1 0.0 Database naming convention - prefix 903 10532654 10532733 2 I am developing a iPhone photo app in which there is one view, where I am showing all the images taken through that app with the help of uiscrollview. First I simply loaded the scrollview with all the present images. But it made the app slow and also caused the crash giving the following warning: Received memory warning. Level=2 I googled a lot and found that the reason for so may be loading such heavy images all together on a view are resulting in memory warning and crash afterwards. So I opt for the concept of lazy loading. In which I was just loading the three images one at the center(currently shown to user) and the other two on either sides. I did that in following way: - (void)scrollViewDidEndDecelerating:(UIScrollView *)scrollView { pageNum = (int)(scrollView.contentOffset.x / scrollView.frame.size.width); pageNumber = floor(pageNum); [self setImages:pageNumber]; //setting three images } Now there is no crash, no memory warning but the scroll has become quite rough with lots of jerks. Please suggest me how to get rid the roughness or to show all the images same as 

#### Clean and preprocess the 'posts' DataFrame, keeping only rows where the 'Tags' column contains "<".


In [0]:
# Data cleaning and preprocessing

df = posts[['id', 'Body', 'Title', 'Tags']]
df = df.filter(instr(col("Tags"), "<") > 0)


#### Concatenate the 'Title' and 'Body' columns to create a new column 'text' in the DataFrame.


In [0]:
# Concatenate 'Title' and 'Body' columns
df = df.withColumn("text", concat(col("Title"), lit(" "), col("Body")))

#### Clean the 'text' column by removing special characters and converting the text to lowercase.


In [0]:
# Clean text: remove special characters, convert to lowercase
df = df.withColumn("text", lower(regexp_replace("text", r"[\W_]+", " ")))


#### Clean the 'Tags' column by removing angle brackets and extra whitespace, and converting the text to lowercase.


In [0]:
# Clean Tags column
df = df.withColumn("Tags", lower(regexp_replace(regexp_replace("Tags", r"[<>]", " "), r"\s+", " ")))


*displays the contents*

In [0]:
df.show()

+--------+--------------------+--------------------+--------------------+--------------------+
|      id|                Body|               Title|                Tags|                text|
+--------+--------------------+--------------------+--------------------+--------------------+
|10531977|<p>Ok, capturing ...|Key code for comm...| javascript keybo...|key code for comm...|
|10510574|<p>I have an appl...|No readline suppo...| python readline ...|no readline suppo...|
|10530232|<p>I know there a...|Database naming c...| database-design ...|database naming c...|
|10532654|<p>I am developin...|With lazy loading...| iphone ios4 uisc...|with lazy loading...|
|10540020|<p>So I have a ni...|Copying objects u...|          c++ c++11 |copying objects u...|
|10537476|"<p>I have a C++ ...|how to compile an...| ios makefile and...|how to compile an...|
|10532840|<p>Is it possible...|How to access rev...| google-apps-script |how to access rev...|
|10540366|<p>I'm trying to ...|using DotNetOpenA..

##### Split the 'Tags' column into an array, filter out empty tags, and expand the array into separate rows.


In [0]:
# Split Tags column into an array
df = df.withColumn("Tags", explode(split(df.Tags, " "))).filter(col("Tags") != '')


##### Shuffle the data in the DataFrame 'df' into 10 partitions.


In [0]:
# Data shuffling
df = df.repartition(10)


##### Use a label encoder to convert the 'Tags' column into a numerical 'label' column.


In [0]:
# Label encoder
label_encoder = StringIndexer(inputCol = "Tags", outputCol = "label", handleInvalid='skip')

label_model = label_encoder.fit(df)
labels = label_model.transform(df)

##### Find the true labels for each post by grouping the labels associated with each post ID.


In [0]:

# Find true labels
temp = labels.withColumnRenamed("id", "id_dup") \
     .groupBy("id_dup").agg(collect_list("label").alias("true_labels"))

true_labels = (labels.join(temp, labels.id == temp.id_dup, 'left_outer'))
     

display(true_labels)
     


id Body Title Tags text label id_dup true_labels 10589332 I'm testing some groovy code that uses a java library and I want to mock out the library calls because they use the network. So the code under test looks something like: def verifyInformation(String information) { def request = new OusideLibraryRequest().compose(information) new OutsideLibraryClient().verify(request) } I tried using MockFor and StubFor but I get errors such as: No signature of method: com.myproject.OutsideLibraryTests.MockFor() is applicable for argument types: (java.lang.Class) values: [class com.otherCompany.OusideLibraryRequest] I'm using Grails 2.0.3. How to mock the 'new' operator constructor how to mock the new operator p i m testing some groovy code that uses a java library and i want to mock out the library calls because they use the network so the code under test looks something like p pre code def verifyinformation string information def request new ousidelibraryrequest compose information new outsidelibraryclient verify request code pre p i tried using mockfor and stubfor but i get errors such as p pre code no signature of method com myproject outsidelibrarytests mockfor is applicable for argument types java lang class values class com othercompany ousidelibraryrequest code pre p i m using grails 2 0 3 p 84.0 10589332 List(301.0, 268.0, 1053.0, 84.0, 158.0) 10589823 I knew, there are thousands of topics similar to mine. I read them all. Nothing works for me. And there I will describe my problem: I created a Oracle database using Oracle SQL developer setting values: connection name: test, username: bob, password: qwerty Connection type: basic, role: default, Hostname: localhost, port: 1521, SID : orcl Reason I'm writing all of this is that I really did everything possible, and I hope that by providing each kind of data someone will be able to help me. My next step was downloading and installing ODAC 11.2 Release 4 (11.2.0.3.0) with Oracle Developer Tools for Visual Studio. When I want make a connection to database from my application using server explorer I'm entering following data: data source name: //localhost:1521/test user name: ADMIN password : qwerty connection name is being set automatically. When I'm trying to test connection I'm getting ORA 12514... and here it is how I changed my tnsname.ora: LISTENER_ORCL = (ADDRESS = (PROTOCOL = TCP)(HOST = localhost)(PORT = 1521)) orcl = (DESCRIPTION = (ADDRESS_LIST = (ADDRESS = (PROTOCOL = TCP)(HOST = localhost)(PORT = 1521)) ) (CONNECT_DATA = (SERVICE_NAME = orcl) ) ) VS 2010 & Oracle 11g ORA 12514 c# vs 2010 oracle 11g ora 12514 p i knew there are thousands of topics similar to mine i read them all nothing works for me and there i will describe my problem i created a oracle database using oracle sql developer setting values p pre code connection name test username bob password qwerty connection type basic role default hostname localhost port 1521 sid orcl code pre p reason i m writing all of this is that i really did everything possible and i hope that by providing each kind of data someone will be able to help me p p my next step was downloading and installing odac 11 2 release 4 11 2 0 3 0 with oracle developer tools for visual studio p p when i want make a connection to database from my application using server explorer i m entering following data p pre code data source name localhost 1521 test user name admin password qwerty code pre p connection name is being set automatically p p when i m trying to test connection i m getting ora 12514 and here it is how i changed my tnsname ora p pre code listener orcl address protocol tcp host localhost port 1521 orcl description address list address protocol tcp host localhost port 1521 connect data service name orcl code pre 1.0 10589823 List(32.0, 37.0, 1.0) 10582190 I have 2 POCO classes: public class Student { public int StudentId { get; set; } public string StudentName { get; set; } public virtual ICollection<Course> Courses { get; set; } } publi

####tokenizes the text, removes stop words, performs stemming, removes additional stop words based on EDA, and then applies count vectorization and TF-IDF to the text data.

In [0]:
# Tokenization
tokenizer = Tokenizer(inputCol="text", outputCol="tokens")
tokenized = tokenizer.transform(true_labels)

# Removing stop words
stopword_remover = StopWordsRemover(inputCol="tokens", outputCol="stop_words")
stopword = stopword_remover.transform(tokenized)

# Stemming
stemmer_func = udf(lambda words: [PorterStemmer().stem(word) for word in words], ArrayType(StringType()))
stemmed = stopword.withColumn("stemmed", stemmer_func(col("stop_words")))

# Removing additional stop words based on EDA
custom_stop_words = ['code', 'use', 'pre', 'get', 'want', 'like', 'thank', 'try', 'work', 'way', 'need']
stopword_remover = StopWordsRemover(inputCol="stemmed", outputCol="filtered", stopWords=custom_stop_words)
filtered = stopword_remover.transform(stemmed)

# Count vectorization
cv = CountVectorizer(vocabSize=8000, inputCol="filtered", outputCol='cv')
cv_model = cv.fit(filtered)
text_cv = cv_model.transform(filtered)

# TF-IDF
idf = IDF(inputCol='cv', outputCol="features", minDocFreq=2)
idf_model = idf.fit(text_cv)
text_idf = idf_model.transform(text_cv)

*Print the schema of the DataFrame 'text_idf'.*


In [0]:
text_idf.printSchema()

root
 |-- id: integer (nullable = true)
 |-- Body: string (nullable = true)
 |-- Title: string (nullable = true)
 |-- Tags: string (nullable = false)
 |-- text: string (nullable = true)
 |-- label: double (nullable = false)
 |-- id_dup: integer (nullable = true)
 |-- true_labels: array (nullable = true)
 |    |-- element: double (containsNull = false)
 |-- tokens: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- stop_words: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- stemmed: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- filtered: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- cv: vector (nullable = true)
 |-- features: vector (nullable = true)



##### Save the preprocessed data DataFrame 'text_idf' to the Databricks local file system for use in the next phase.


In [0]:
# Checkpoint for next phase
text_idf.write.mode('overwrite').parquet("/tmp/project/preprocessed_data")



##### Read the preprocessed data from the Parquet file into a DataFrame named 'preprocessed_data' and print its schema.

In [0]:
# Read the preprocessed data from the Parquet file into a DataFrame
preprocessed_data = spark.read.parquet("/tmp/project/preprocessed_data")

# Display the contents of the DataFrame
preprocessed_data.printSchema()

root
 |-- id: integer (nullable = true)
 |-- Body: string (nullable = true)
 |-- Title: string (nullable = true)
 |-- Tags: string (nullable = true)
 |-- text: string (nullable = true)
 |-- label: double (nullable = true)
 |-- id_dup: integer (nullable = true)
 |-- true_labels: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- tokens: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- stop_words: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- stemmed: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- filtered: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- cv: vector (nullable = true)
 |-- features: vector (nullable = true)



##### Save the preprocessing models for label encoding, count vectorization, and TF-IDF to the specified locations in the Azure blob storage.

In [0]:
# Save preprocessing models
label_model.write().overwrite().save('/mnt/mydatalakefilesystem/Capstone2/Models/stringindexer')
cv_model.write().overwrite().save('/mnt/mydatalakefilesystem/Capstone2/Models/cv_model')
idf_model.write().overwrite().save("/mnt/mydatalakefilesystem/Capstone2/Models/tfidf")